In [39]:
from __future__ import print_function, division

from keras.datasets import mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, GlobalAveragePooling2D, MaxPooling2D
from keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import Adam

import matplotlib.pyplot as plt

import numpy as np
from scipy.misc import imread
from scipy.misc import imresize
from scipy.misc import imsave
import glob
import random

from keras.preprocessing.image import ImageDataGenerator
from keras import applications
from keras.optimizers import SGD
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras.callbacks import EarlyStopping
from keras.utils import to_categorical
#from keras.applications.resnet50 import preprocess_input

from keras.applications.resnet50 import ResNet50
from keras.preprocessing import image
from keras.applications.resnet50 import preprocess_input, decode_predictions
#from keras.applications.vgg19 import preprocess_input as preprocess_vgg
from keras.applications.inception_v3 import preprocess_input as inception_preprocess

#from keras.applications.inception_resnet_v2 import preprocess_input

import numpy as np

import keras
import copy
import cv2

from keras.models import *
from keras.layers import *
from keras.optimizers import *

import numpy as np 
import os
import numpy as np
from keras.callbacks import ModelCheckpoint, LearningRateScheduler
from keras import backend as keras

In [40]:
path = '../data/'
savepath = '../data/'
images = glob.glob(path+'new_data/*.npy')

In [41]:
tile_sizes = np.loadtxt(path+'tile_sizes.txt', dtype='int')
tile_sizes = tile_sizes[:150]
images_sampled = {}
for tile in tile_sizes:
    for i in range(1, 31):
        images_sampled.setdefault(tile[0]*30+i, []).append(tile[1])

In [42]:
def myGenerator(batch_size):
    while True:
        index_list = random.sample(images_sampled.keys(), batch_size)
        alldata_x = []
        alldata_y = []
        for i in index_list:
            frame = path+'sources/nparrs_384/frame'+str(i)+'.npy'
            frame = np.load(frame)
            tile_index = random.choice(images_sampled[i])
            
            temp  = imresize(frame[tile_index], (48, 48))
            temp  = imresize(temp, (384, 384))
            
            alldata_x.append(temp)
            alldata_y.append(frame[tile_index])
        
        alldata_x = np.array(alldata_x)
        alldata_y = np.array(alldata_y)
        
        alldata_y = (alldata_y.astype(np.float32) - 127.5) / 127.5
        alldata_x = alldata_x.astype(np.float32)/255.0
        
        yield alldata_x, alldata_y

#x = myGenerator(10)
#xtrain, ytrain = next(x)
#print('xtrain shape:',xtrain.shape)
#print('ytrain shape:',ytrain.shape)

In [43]:
class CGAN():
    def __init__(self):
        # Input shape
        self.img_rows = 384
        self.img_cols = 384
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminator
        #self.discriminator = self.build_discriminator()
        #self.discriminator.compile(loss=['mse'],
        #    optimizer=optimizer,
        #    metrics=['accuracy'])
        
        #print(self.discriminator.summary())
        
        # Build the generator
        self.generator = self.build_generator()
        
        print(self.generator.summary())
        
        noise = Input(shape=(384, 384, 3))
        img = self.generator(noise)

        # For the combined model we will only train the generator
        #self.discriminator.trainable = False

        # The discriminator takes generated image as input and determines validity
        # and the label of that image
        #valid = self.discriminator(img)
        
        # The combined model  (stacked generator and discriminator)
        # Trains generator to fool discriminator
        #self.combined = Model(noise, [img, valid])
        #self.combined.compile(loss=['mse', 'mse'],
        #    loss_weights=[0.9, 0.1],
        #    optimizer=optimizer)

    def build_generator(self):
        input_size = (384,384,3)
        inputs = Input(input_size)


        conv1 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(inputs)
        conv1 = LeakyReLU()(conv1)
        conv1 = BatchNormalization(momentum=0.8)(conv1)



        conv2 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv1)
        conv2 = LeakyReLU()(conv2)
        conv2 = BatchNormalization(momentum=0.8)(conv2)

        conv3 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv2)
        conv3 = LeakyReLU()(conv3)
        conv3 = BatchNormalization(momentum=0.8)(conv3)

        concat1 = add([conv1, conv3])



        conv4 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat1)
        conv4 = LeakyReLU()(conv4)
        conv4 = BatchNormalization(momentum=0.8)(conv4)

        conv5 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv4)
        conv5 = LeakyReLU()(conv5)
        conv5 = BatchNormalization(momentum=0.8)(conv5)

        concat2 = add([conv5, concat1])



        conv6 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat2)
        conv6 = LeakyReLU()(conv6)
        conv6 = BatchNormalization(momentum=0.8)(conv6)

        conv7 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv6)
        conv7 = LeakyReLU()(conv7)
        conv7 = BatchNormalization(momentum=0.8)(conv7)

        concat3 = add([conv7, concat2])



        conv8 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat3)
        conv8 = LeakyReLU()(conv8)
        conv8 = BatchNormalization(momentum=0.8)(conv8)

        conv9 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv8)
        conv9 = LeakyReLU()(conv9)
        conv9 = BatchNormalization(momentum=0.8)(conv9)
        

        conv10 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv9)
        conv10 = LeakyReLU()(conv10)
        conv10 = BatchNormalization(momentum=0.8)(conv10)

        concat4 = add([conv10, conv1])
        
        conv11 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(concat4)
        conv11 = LeakyReLU()(conv11)
        conv11 = BatchNormalization(momentum=0.8)(conv11)
        
        conv12 = Conv2D(8, 3, padding = 'same', kernel_initializer = 'he_normal')(conv11)
        conv12 = LeakyReLU()(conv12)
        conv12 = BatchNormalization(momentum=0.8)(conv12)


        out = Conv2D(3, 3, padding = 'same', kernel_initializer = 'he_normal')(conv12)
        out = LeakyReLU()(out)
        out = BatchNormalization(momentum=0.8)(out)


        model = Model(input = inputs, output = out)
        return model
    
    def build_autoencoder(self):
        self.generator.compile(loss=['mse'],optimizer=self.optimizer)
    
    def train_generator_autoencoder(self, epochs, batch_size=128, sample_interval=10):
        for epoch in range(epochs):
            X_train, y_train = next(myGenerator(batch_size))
            g_loss = self.generator.train_on_batch(X_train, y_train)
            print ("Epoch ", epoch, " G loss ", g_loss)
            if epoch % sample_interval == 0:
                self.sample_images(epoch)
                self.generator.save_weights(savepath+'weights/generator_weights_'+str(epoch)+'.h5')

    def sample_images(self, epoch):
        r, c             = 1, 10
        X_train, y_train = next(myGenerator(10))
        gen_imgs         = self.generator.predict(X_train)
        
        # Rescale images 0 - 1
        temp     = (0.5 * gen_imgs + 0.5)*255
        gen_imgs = temp.astype(int)
        y_train = (0.5 * y_train + 0.5)*255
        y_train = y_train.astype(int)
        X_train = X_train*255
        X_train = X_train.astype(int)
        
        combined = np.array([gen_imgs[0], gen_imgs[1], gen_imgs[2], gen_imgs[3], gen_imgs[4], gen_imgs[5], gen_imgs[6], gen_imgs[7], gen_imgs[8], gen_imgs[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+".png", combined)
        
        combined = np.array([y_train[0], y_train[1], y_train[2], y_train[3], y_train[4], y_train[5], y_train[6], y_train[7], y_train[8], y_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_real.png", combined)
        
        combined = np.array([X_train[0], X_train[1], X_train[2], X_train[3], X_train[4], X_train[5], X_train[6], X_train[7], X_train[8], X_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_lowres.png", combined)

In [44]:
cgan = CGAN()
cgan.build_autoencoder()
cgan.train_generator_autoencoder(200000, 10, 100)

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:116: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("ba...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_15 (InputLayer)           (None, 384, 384, 3)  0                                            
__________________________________________________________________________________________________
conv2d_86 (Conv2D)              (None, 384, 384, 8)  224         input_15[0][0]                   
__________________________________________________________________________________________________
leaky_re_lu_72 (LeakyReLU)      (None, 384, 384, 8)  0           conv2d_86[0][0]                  
__________________________________________________________________________________________________
batch_normalization_86 (BatchNo (None, 384, 384, 8)  32          leaky_re_lu_72[0][0]             
__________________________________________________________________________________________________
conv2d_87 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':


Epoch  0  G loss  1.0184677


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:146: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:150: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:154: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.


...

Epoch  134930  G loss  0.065991364
Epoch  134931  G loss  0.048572637
Epoch  134932  G loss  0.039978843
Epoch  134933  G loss  0.013878008
Epoch  134934  G loss  0.031018207
Epoch  134935  G loss  0.04347828
Epoch  134936  G loss  0.05465286
Epoch  134937  G loss  0.03217142
Epoch  134938  G loss  0.05605079
Epoch  134939  G loss  0.010567189
Epoch  134940  G loss  0.027151551
Epoch  134941  G loss  0.028283808
Epoch  134942  G loss  0.019737773
Epoch  134943  G loss  0.010489171
Epoch  134944  G loss  0.017229209
Epoch  134945  G loss  0.013002458
Epoch  134946  G loss  0.03354469
Epoch  134947  G loss  0.016584031
Epoch  134948  G loss  0.036323227
Epoch  134949  G loss  0.015303316
Epoch  134950  G loss  0.021647578
Epoch  134951  G loss  0.031684652
Epoch  134952  G loss  0.09022133
Epoch  134953  G loss  0.021866169
Epoch  134954  G loss  0.056585323
Epoch  134955  G loss  0.022396445
Epoch  134956  G loss  0.051710248
Epoch  134957  G loss  0.014463194
Epoch  134958  G loss  0.0

Epoch  135167  G loss  0.042227723
Epoch  135168  G loss  0.037929796
Epoch  135169  G loss  0.01747031
Epoch  135170  G loss  0.014504507
Epoch  135171  G loss  0.021417264
Epoch  135172  G loss  0.03058048
Epoch  135173  G loss  0.018409804
Epoch  135174  G loss  0.091444224
Epoch  135175  G loss  0.011944116
Epoch  135176  G loss  0.021186015
Epoch  135177  G loss  0.01424666
Epoch  135178  G loss  0.029539865
Epoch  135179  G loss  0.011804002
Epoch  135180  G loss  0.012477646
Epoch  135181  G loss  0.016294504
Epoch  135182  G loss  0.022567412
Epoch  135183  G loss  0.061465006
Epoch  135184  G loss  0.017191049
Epoch  135185  G loss  0.030909989
Epoch  135186  G loss  0.061093993
Epoch  135187  G loss  0.015879203
Epoch  135188  G loss  0.016589632
Epoch  135189  G loss  0.026462555
Epoch  135190  G loss  0.016342979
Epoch  135191  G loss  0.018762123
Epoch  135192  G loss  0.015445618
Epoch  135193  G loss  0.011781443
Epoch  135194  G loss  0.031740643
Epoch  135195  G loss  

Epoch  135404  G loss  0.015580356
Epoch  135405  G loss  0.0140422005
Epoch  135406  G loss  0.067928456
Epoch  135407  G loss  0.1412997
Epoch  135408  G loss  0.01369373
Epoch  135409  G loss  0.053238124
Epoch  135410  G loss  0.008894553
Epoch  135411  G loss  0.014933315
Epoch  135412  G loss  0.042686522
Epoch  135413  G loss  0.19961324
Epoch  135414  G loss  0.026233438
Epoch  135415  G loss  0.042598873
Epoch  135416  G loss  0.026790332
Epoch  135417  G loss  0.024681682
Epoch  135418  G loss  0.036831483
Epoch  135419  G loss  0.06614739
Epoch  135420  G loss  0.05779816
Epoch  135421  G loss  0.011399854
Epoch  135422  G loss  0.1266174
Epoch  135423  G loss  0.011938257
Epoch  135424  G loss  0.039128624
Epoch  135425  G loss  0.024807233
Epoch  135426  G loss  0.01951266
Epoch  135427  G loss  0.017977852
Epoch  135428  G loss  0.06583716
Epoch  135429  G loss  0.026534606
Epoch  135430  G loss  0.029161355
Epoch  135431  G loss  0.02204835
Epoch  135432  G loss  0.02484

Epoch  135640  G loss  0.014183879
Epoch  135641  G loss  0.024719276
Epoch  135642  G loss  0.068124235
Epoch  135643  G loss  0.007879021
Epoch  135644  G loss  0.017779887
Epoch  135645  G loss  0.06666003
Epoch  135646  G loss  0.024748314
Epoch  135647  G loss  0.05929575
Epoch  135648  G loss  0.02487523
Epoch  135649  G loss  0.008555947
Epoch  135650  G loss  0.013184872
Epoch  135651  G loss  0.00796354
Epoch  135652  G loss  0.008204935
Epoch  135653  G loss  0.052231543
Epoch  135654  G loss  0.014120633
Epoch  135655  G loss  0.020434178
Epoch  135656  G loss  0.01643605
Epoch  135657  G loss  0.01158807
Epoch  135658  G loss  0.014369379
Epoch  135659  G loss  0.012433626
Epoch  135660  G loss  0.0695114
Epoch  135661  G loss  0.013112107
Epoch  135662  G loss  0.008388124
Epoch  135663  G loss  0.113599956
Epoch  135664  G loss  0.032306742
Epoch  135665  G loss  0.009361716
Epoch  135666  G loss  0.061730396
Epoch  135667  G loss  0.031576317
Epoch  135668  G loss  0.008

KeyboardInterrupt: 

In [31]:
for i in range(1000):
    x = myGenerator(1)
    xtest, ytest = next(x)
    pred = cgan.generator.predict(xtest)
    pred = pred*127.5 + 127.5
    pred = pred.astype(int)
    #plt.imshow(pred[0])
    #plt.show()
    ytest = ytest*127.5+127.5
    ytest = ytest.astype(int)
    #plt.imshow(ytest[0])
    #plt.show()
    imsave(path+'test/frame_pred'+str(i)+'.png', pred[0])
    imsave(path+'test/frame_real'+str(i)+'.png', ytest[0])

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:13: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  del sys.path[0]
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:14: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  


In [32]:
import numpy 
import math
import cv2

def psnr(img1, img2):
    mse = numpy.mean( (img1 - img2) ** 2 )
    if mse == 0:
        return 100
    PIXEL_MAX = 255.0
    return 20 * math.log10(PIXEL_MAX / math.sqrt(mse))

In [36]:
data = []
for i in range(1000):
    img1 = cv2.imread(path+'test/frame_real'+str(i)+'.png')
    img2 = cv2.imread(path+'test/frame_pred'+str(i)+'.png')
    d = psnr(img1, img2)
    data.append(d)
print('PSNR:', np.mean(data))

PSNR: 31.612699630864867
